# Analyzing The Wanderers

This notebook analyzes the ["The Wanderers"](https://wanderers.ai/) NFT collection with a focus on their traits and the prices they can realize. [Visit the repository](https://github.com/ymyke) for more notebooks on other projects, to use the code, or to contribute.

Important: This notebook uses [Plotly](https://plotly.com/python/) mostly to visualize data. Plotly charts won't be rendered in Githubs notebook viewer. So please [view this notebook on nbviewer](https://nbviewer.org/github/ymyke/niftylytics/blob/main/the_wanderers.ipynb) (or on your local installation after cloning the repo). Note that nbviewer caches notebooks and sometimes takes a long time to pick up a new version.

On the upside, all the Plotly charts are interactive. You can zoom, hover, pan, etc. Zooming is especially important due to the outliers in some the data so you can zoom in on the interesting parts.

Note also that the Plotly charts take a long time to load in the browser because there are a lot of charts with many data points.

In [1]:
import plotly.io as pio
pio.renderers.default = "notebook_connected"

## Get the assets

Note that this takes a long time, i.e. up to 10 minutes. Also note the timestamp below,
that is when the information was last retrieved.

In [2]:
import datetime
from opensea import retrieve_assets

ids = list(range(0, 8888))
assets = retrieve_assets(token_ids=ids, contract="0x8184a482A5038B124d933B779E0Ea6e0fb72F54E")
print(datetime.datetime.now())


............................................................................................................................................................................................................................................................................................................................................................................................................................................................. -- All 8888 assets retrieved.
2022-01-09 13:46:53.608468


## Build a dataframe

Check the trait types there are. We'll see that 1) different assets can have different numbers of traits, 2) the same asset can have traits with the same name, i.e. "Celestial Body".

In [3]:
[", ".join(t["trait_type"] for t in a["traits"]) for a in assets][:10]

['Planet, Anomaly, Music, Cockpit, Left Arm, Window, Celestial Body, Celestial Body, Panel 3, Ships, Right Arm, Panel 4, Panel 2',
 'Planet, Cockpit, Left Arm, Right Arm, Window, Celestial Body, Music, Panel 1, Celestial Body',
 'Window, Left Arm, Music, Panel 2, Cockpit, Right Arm, Panel 4, Planet, Celestial Body',
 'Panel 2, Left Arm, Panel 1, Panel 3, Panel 4, Cockpit, Music, Window, Right Arm, Celestial Body',
 'Anomaly, Panel 5, Ships, Cockpit, Right Arm, Celestial Body, Window, Music, Left Arm',
 'Panel 4, Celestial Body, Window, Celestial Body, Right Arm, Cockpit, Music, Panel 5, Left Arm',
 'Panel 1, Panel 4, Cockpit, Right Arm, Ships, Window, Music, Left Arm, Panel 3',
 'Cockpit, Panel 3, Panel 4, Right Arm, Panel 5, Music, Window, Left Arm',
 'Cockpit, Right Arm, Left Arm, Panel 1, Ships, Panel 5, Window, Music',
 'Panel 4, Ships, Right Arm, Planet, Panel 3, Cockpit, Left Arm, Window, Celestial Body, Music, Celestial Body']

All the possible celestial bodies there are:

In [4]:
set([t["value"]  for a in assets for t in a["traits"] if t["trait_type"] == "Celestial Body"])

{'Blue Galaxy',
 'Blue Stars',
 'Green Stars',
 'Large Green Galaxy',
 'Large Purple Galaxy',
 'Purple Galaxy',
 'Purple Stars',
 'Red Stars'}

We will count the number of Celestial Bodies as well as the number of stars and galaxies when tabulating all the information into a dataframe:

(Large vs not large galaxies will be ignored; could be added as some point in the future.)

In [5]:
import numpy as np
import pandas as pd
import helpers
df, traits = helpers.turn_assets_into_df_wanderers_variant(assets)
hoverdata = [ "Name", *traits, "Probscore"]

In [6]:
assert set(df.LPsymbol.unique()) == set(["ETH", "WETH", np.nan]), """
This sheet does not do currency conversion at the moment and therefore 
assumes all prices are in (W)ETH. But there are more symbols in the input 
data which would lead to apples being compared to ranges below. Aborting.
"""

## How many pieces have a last price on OpenSea?

In [7]:
print(f"{df[~df.Lastprice.isna()].shape[0] / df.shape[0]:.0%}")

80%


## How are prices evolving over time?

Note that this only takes into account the last sale of each piece.

In [8]:
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt

plt.rcParams["figure.figsize"] = (20, 8)
pd.plotting.register_matplotlib_converters()

fig = px.scatter(df, x="LPdate", y="Lastprice", hover_data=hoverdata)
fig.show()

## Price levels today

In [9]:
fig = px.histogram(df, x="Lastprice", marginal="box", hover_data=hoverdata)
fig.show()

## How frequent are the different traits?

In [10]:
pd.set_option("display.max_columns", None)

from IPython.display import display
for trait in sorted(traits.keys()):
    display(
        pd.DataFrame(df[trait].value_counts(normalize=False, sort=True, ascending=True)).transpose()
    )


Monolith  Purple Wormhole  Glitch Wormhole  White Wormhole  \
Anomaly        63              233              241             246   

         Blue Wormhole  Pink Wormhole     -  
Anomaly            255            258  7592

6  5    4    3     2     0     1
Celestial Bodies  2  9  100  528  1892  2889  3468

Cat   -  Glyphs  Hexagon  Sound  Dots  Chart  Retro  Falcon  Circles  \
Cockpit   82  90     174      669    682   701    706    708     711      721   

         Pink  Target  Dotface  Radar  Planet  
Cockpit   724     725      725    731     739

3    2     1     0
Galaxies  31  313  2407  6137

Joint  ETH  Skull  Jar Eyes  Porn  Jar Shrooms  Alien Joint  Hotdog  \
Left Arm     24   33     34        36    37           39           42      44   

          Robo Charge  Goldfish  Bong  Whiskey  8-Ball  Takeout  Banana  \
Left Arm           44        66    81       84      85       87      87   

          Pizza  Chicken  Syringe  Orbit  Watch  Hook  Jar   -  Booze  Knife  \
Left Arm     89       89       90     90     90    90   90  90     92     93   

          Coffee  Bone  Flag  Egg  Burn  Boba  Wine  Flower  Shrooms  Laser  \
Left Arm      93    94    98   98    99   101   106     106      107    108   

          Zombie  Treasure  Slider  V Steering  Shifter  Hologram  Tablet  \
Left Arm     112       342     347         369      370       373     373   

          Antennae  Handcrank  Thrust  Big Button  Swipe  Button Row Slider  \
Left Arm       377        378     381         385    385                387   

          Buttons  Alien Gearshift  Button Row  Gearshift  
Left Arm      391              392         394        396

...

ETH  Joint  Jar Shrooms  Skull  Porn  Alien Joint  Hotdog  \
Right Arm   31     31           32     36    40           40      40   

           Robo Charge  Jar Eyes  Jar  Knife  Flag  Bong  Orbit  8-Ball  \
Right Arm           41        41   79     79    82    83     84      84   

           Pizza  Zombie  Banana  Bone   -  Egg  Boba  Syringe  Whiskey  Hook  \
Right Arm     87      88      89    89  90   95    97       97       98   100   

           Takeout  Coffee  Wine  Laser  Shrooms  Watch  Goldfish  Booze  \
Right Arm      100     100   100    102      104    105       106    106   

           Burn  Flower  Chicken  Alien Gearshift  Handcrank  Hologram  \
Right Arm   107     109      109              315        330       335   

           Slider  Swipe  Tablet  Buttons  Button Row Slider  Gearshift  \
Right Arm     350    363     376      377                379        383   

           V Steering  Antennae  Shifter  Thrust  Big Button  Treasure  \
Right Arm         384       390      390     396         397       405   

           Button Row  
Right Arm         417

Space Station  Guardian (active)  Large Battle  Cargo  Flyby Trio  \
Ships            145                155           157    173         174   

       Guardian (rogue)  Battle (alt)  Triforce  Flyby Dogfight  \
Ships               175           178       188             188   

       Destroyed Freighter  Flyby  UFO  Battle  Docking  Fleet  Freighter  \
Ships                  188    189  189     190      195    196        197   

       Freighter Battle     -  
Ships               210  5801

4    3     2     1     0
Stars  6  157  1098  3476  4151

-  Tubes  Eyes  ETH  Plants  Blue  Screens  Green  White  Bolt  \
Window  90    186   199  215     430   733      737    760    769   777   

        Wires  Crack  Purple  Pink  Dice  
Window    781    786     786   809   830

Guardian Marked, RADIOACTIVE  Warp Squad Sixteen  Guardian Marked  \
special                             1                  16               41   

         RADIOACTIVE     -  
special           82  8748

## How much do people pay for the different traits?

**Some Observations**:

- The monolith anomaly commands much higher prices than other anomalies. It is also the most seldom anomaly.
- The more celestial bodies, the higher the price. Same with galaxies and stars. (4 stars is really seldom and outperforms 0-3 stars massively.)
- A cat cockpit slightly outperforms other cockpits. Interestingly, glyphs perform average, even though they are much rarer than average. No cockpit at all has a bad impact on price.
- Arms: Joints perform best, followed by ETH, bong, porn, alien joint, and skull. Flag is clearly worst (I wonder why?). Bongs perform much better than their rarity would suggest, whereas flags left perform much worse than their rarity would suggest (not so much for flags right, strangely).
- Music doesn't make a difference. Except no music at all, which is detrimental to price.
- Panels: Crypto, bounty, tetris, spam are the best preformers which is very much in line with their rarity.
- Planet: Anger orb and destroyed planet are clearly performing best and also rarest.
- Ships: Doesn't make much of a difference.
- Window: Doesn't make much of a difference.
- Special: Specials in general add to the value. Warp squad sixteen performs very high.
- Keep in mind that this doesn't take into account possible cross-correlations between the different traits. 


In [11]:
for trait in sorted(traits.keys()):

    fig = go.Figure()

    for traitvariant in (
        df.groupby(trait).median().sort_values("Lastprice", ascending=False).index
        ):
        fig.add_trace(
            go.Box(
                y=df[df[trait] == traitvariant].fillna("-").Lastprice.values,
                name=traitvariant,
                # boxpoints="all",
                jitter=0.2,
                whiskerwidth=0.2,
                marker_size=2,
                line_width=1,
            )
        )
    fig.update_layout(title=trait)
    fig.show()

## What is pricier, galaxies or stars?

There seems to be no fundamental difference between stars and galaxies. In either case, rarity is the differentiator: 3 galaxies is slightly rare, 4 stars is rare, 5 bodies overall is rare and 6 bodies is superrare – so these all command higher prices.

In [12]:
df["Celestialstype"] = df.apply(
    lambda x: "Starsonly"
    if x["Galaxies"] == 0
    else "Galaxiesonly"
    if x["Stars"] == 0
    else "Both",
    axis=1,
)
px.box(df, x="Celestial Bodies", y="Lastprice", color="Celestialstype", points="all", hover_data=hoverdata)

## Check if there's a bargain for any of the more lucrative traits

In [13]:
display(df[df["Anomaly"] != "-"].sort_values("Price").head(3))
display(df[df["Celestial Bodies"] >= 4].sort_values("Price").head(3))
display(df[df["Left Arm"].isin(["Joint", "Alien Joint", "Bong", "Skull", "Porn", "ETH"])].sort_values("Price").head(3))
# ...

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
7779  7779  0.250     ETH     0.1600      ETH 2021-08-15 18:08:06   0.838234   
4023  4023  0.269     ETH        NaN      NaN                 NaT   0.002587   
3078  3078  0.285     ETH     0.2599      ETH 2021-12-06 07:34:39   0.073315   

             Anomaly  Celestial Bodies Cockpit  Galaxies Left Arm  \
ID                                                                  
7779   Blue Wormhole                 2    Pink         1    Orbit   
4023  White Wormhole                 0  Glyphs         0    Swipe   
3078   Pink Wormhole                 1   Radar         0  Buttons   

             Music      Panel 1 Panel 2 Panel 3 Panel 4   Panel 5  \
ID                                                                  
7779   Star Ranger            -    Trim       -       -         -   
4023   Space Ender  Waves (alt)       -  Tunnel       -  Hexagons   
3078  The Wayfarer            -    Code    Data   Waves         -   

                     Planet   Right Arm Ships  Stars  Window special  \
ID                                                                     
7779                      -  Big Button     -      1   Wires       -   
4023  Large Purple (bottom)    Antennae     -      0    Bolt       -   
3078                      -  Button Row     -      1  Purple       -   

                                                   Link Celestialstype  
ID                                                                      
7779  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
4023  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
3078  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly

Name   Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                              
7999  7999  0.5900     ETH       0.51     WETH 2021-10-19 16:32:32  37.757135   
3374  3374  0.6000     ETH       0.50      ETH 2021-08-26 17:15:45   0.099497   
760    760  0.6998     ETH       0.70      ETH 2021-08-28 00:48:48   0.000481   

              Anomaly  Celestial Bodies Cockpit  Galaxies Left Arm  \
ID                                                                   
7999                -                 4   Retro         1   Thrust   
3374  Purple Wormhole                 4   Radar         2     Bong   
760                 -                 4  Falcon         2  Shifter   

               Music Panel 1    Panel 2 Panel 3 Panel 4  Panel 5  \
ID                                                                 
7999  Lone Planeteer       -          -     DNA       -        -   
3374    The Wanderer   Waves          -   Noisy       -        -   
760     The Wayfarer  Tetris  Particles       -   Crack  Sliders   

                Planet  Right Arm Ships  Stars  Window special  \
ID                                                               
7999                 -  Gearshift     -      3   White       -   
3374                 -     Slider     -      2  Purple       -   
760   Large Blue (top)      Knife     -      2   White       -   

                                                   Link Celestialstype  
ID                                                                      
7999  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
3374  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
760   https://opensea.io/assets/0x8184a482a5038b124d...           Both

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
1130  1130   0.55     ETH      1.250      ETH 2021-09-23 15:55:54   0.000156   
381    381   0.60     ETH        NaN      NaN                 NaT   0.082624   
5374  5374   0.60     ETH      0.439      ETH 2021-10-16 22:07:35   0.021054   

     Anomaly  Celestial Bodies  Cockpit  Galaxies Left Arm           Music  \
ID                                                                           
1130       -                 1   Falcon         1    Skull    The Ponderer   
381        -                 2  Hexagon         0     Bong    The Wayfarer   
5374       -                 1    Retro         0     Bong  Cosmic Drifter   

          Panel 1        Panel 2            Panel 3            Panel 4  \
ID                                                                       
1130  Waves (alt)         Mosaic                  -  Pulselights (alt)   
381             -  Radial Static              Waves                  -   
5374      Loading              -  Pulselights (alt)                  -   

     Panel 5               Planet   Right Arm          Ships  Stars  Window  \
ID                                                                            
1130       -  Asteroid Belt (alt)  Big Button        Docking      0     ETH   
381        -     Large Blue (top)      Tablet              -      2  Plants   
5374       -     Large Blue (top)     Buttons  Space Station      1  Purple   

     special                                               Link Celestialstype  
ID                                                                              
1130       -  https://opensea.io/assets/0x8184a482a5038b124d...   Galaxiesonly  
381        -  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
5374       -  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly